In [1]:
from sentence_transformers import SentenceTransformer, models

/home/erko/.local/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
model_name = "paraphrase-multilingual-mpnet-base-v2"

model = SentenceTransformer(model_name)

In [3]:
import os
import numpy as np
import pandas as pd
import re
from bs4 import BeautifulSoup
import umap

In [4]:
# The directory where data is located
data_dir = "test_data/22_23/"
data = []
for file in os.listdir(data_dir):
    if file.endswith(".txt"):
        with open(data_dir+file,"r") as f:
            data.append([])
            for line in f.readlines():
                data[-1].append(line)

data = np.array(data)

# Print first and last data points
#print(data[0])
#print(data[-1])

# Get only speeches
speeches = data[:,1]

In [46]:
paragraphs = []
for s in speeches:
    soup = BeautifulSoup(s, 'html.parser')
    ps = soup.find_all("p")
    for p in ps:
        paragraphs.append(p.get_text())

print(len(paragraphs))

# Small training set to test
training_set = paragraphs[:5000]

49071


In [6]:
# Extremely small training set
small_training_set = training_set[:100]

In [47]:
# Embeddings

embeddings = model.encode(training_set, show_progress_bar=True)
print(embeddings)

Batches: 100%|██████████| 157/157 [29:01<00:00, 11.09s/it]


[[ 0.063858    0.15769948 -0.00961994 ...  0.09974433 -0.08607417
   0.0076523 ]
 [-0.08792578  0.0596008  -0.01949571 ...  0.00774629  0.07045314
   0.01264617]
 [-0.02793774  0.07232784 -0.0119273  ...  0.0215125  -0.0107824
   0.09849365]
 ...
 [ 0.03413501  0.09187511 -0.01539702 ...  0.04677017 -0.00473724
   0.09749343]
 [ 0.00023169 -0.02349394 -0.01108899 ... -0.01557691 -0.0175232
   0.05868177]
 [-0.05051612 -0.12126688 -0.01387521 ... -0.01327679  0.16639352
  -0.08496522]]


In [8]:
print(len(embeddings[0]))

768


In [9]:
# Sentence similarities
from sentence_transformers import util

In [25]:
#Compute cosine similarity between all pairs
cos_sim = util.cos_sim(embeddings, embeddings)

#Add all pairs to a list with their cosine similarity score
all_sentence_combinations = []
for i in range(len(cos_sim)-1):
    for j in range(i+1, len(cos_sim)):
        all_sentence_combinations.append([cos_sim[i][j], i, j])

#Sort list by the highest cosine similarity score
all_sentence_combinations = sorted(all_sentence_combinations, key=lambda x: x[0], reverse=True)

Top-20 most similar pairs:


IndexError: list index out of range

In [39]:
print("Top-20 most similar pairs:")
for score, i, j in all_sentence_combinations:
    if 0.6 < cos_sim[i][j] < 0.9:
        print("First sentence: {} \n Second sentence: {} \n Similarity: {:.4f}".format(training_set[i], training_set[j], cos_sim[i][j]))

Top-20 most similar pairs:
First sentence: Det första är att Sverige har fått en minister för civilt försvar. Det är viktigt och visar att regeringen prioriterar frågorna om civilt försvar - ett statsråd som helt och fullt kan koncentrera sig på området. Regeringen samlar också ihop delar som rör totalförsvaret som tidigare varit utspridda på olika departement. Nu hamnar de alla under Försvarsdepartementet. Det kommer att underlätta samordningen och höja tempot, vilket är viktigt, och också stärka uppföljningen och genomförandet. Det civila försvaret spänner som bekant över hela samhället. 
 Second sentence: Sverige har med den här regeringen äntligen fått en minister för civilt försvar och återinfört frågorna om det civila försvaret till Försvarsdepartementet. Vi tycker att det är bra, och vi tror att det är klokt att synkronisera dessa frågor så att man tillsammans bättre kan bygga ett starkt totalförsvar. 
 Similarity: 0.8976
First sentence: Vänsterpartiet menar att Sverige bör verk

<p> Now let's try clustering these embeddings. </p>

In [63]:
umap_embeddings = umap.UMAP(n_neighbors=10, 
                            n_components=10, 
                            metric='cosine').fit_transform(embeddings)

<p> Cluster with hdbscan:</p>

In [64]:
import hdbscan
cluster = hdbscan.HDBSCAN(min_cluster_size=15,
                          metric='euclidean',                      
                          cluster_selection_method='eom').fit(umap_embeddings)

<p>Visualize: </p>

In [70]:
import matplotlib.pyplot as plt
# Prepare data
umap_data = umap.UMAP(n_neighbors=15, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
result = pd.DataFrame(umap_data, columns=['x', 'y'])
result['labels'] = cluster.labels_

# Visualize clusters
fig, ax = plt.subplots(figsize=(20, 10))
outliers = result.loc[result.labels == -1, :]
clustered = result.loc[result.labels != -1, :]
plt.scatter(outliers.x, outliers.y, color='#BDBDBD', s=0.5)
plt.scatter(clustered.x, clustered.y, c=clustered.labels, s=0.5, cmap='hsv_r')
plt.colorbar()

<IPython.core.display.Javascript object>

In [69]:
plt.close()
plt.show()